In [1]:
import re
import os
from glob import glob

from langchain_chroma import Chroma
from langchain_core.documents import Document
from langchain.prompts import ChatPromptTemplate
from langchain_core.runnables import RunnablePassthrough
from langchain_openai import OpenAIEmbeddings, ChatOpenAI
from langchain_core.output_parsers import StrOutputParser
from langchain_community.document_loaders import PyMuPDFLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter

from dotenv import load_dotenv
load_dotenv()

True

In [2]:
CHUNK_SIZE = 1000
CHUNK_OVERLAP = 0
MODEL_NAME  = 'gpt-4o-mini'
EMBEDDING_NAME = 'text-embedding-3-large'

COLLECTION_NAME = 'korean_history'
PERSIST_DIRECTORY= 'vector_store/korean_history_db'
name = ["고대", "고려", "근대", "조선", "현대"]

In [3]:
# Split
splitter = RecursiveCharacterTextSplitter.from_tiktoken_encoder(
    model_name=MODEL_NAME,
    chunk_size=CHUNK_SIZE,
    chunk_overlap=CHUNK_OVERLAP,
)

In [5]:
# db 생성
for i in name:
    file = glob(f"./pdf/사건/{i}/*.pdf")
    document_list = []
    for path in file:
        loader = PyMuPDFLoader(path)
        load_docs = loader.load()
        full_text = [doc.page_content for doc in load_docs] 
        full_text = ''.join(full_text)
        full_text = re.sub(r"관련사료", "", full_text)
        full_text = re.sub(r"\([一-龥]+\)", "", full_text)
        full_text = re.sub(r"\n", "", full_text)

        docs = splitter.split_text(full_text)
        id = "_".join(os.path.splitext(os.path.basename(path))[0].split('_')[:2])
        title = os.path.splitext(os.path.basename(path))[0].split('_')[-1]
        metadata = {
        "id":id,
        "title": title,
        "full_text": full_text
        }

        for doc in docs:
            _doc = Document(metadata=metadata, page_content=doc)
            document_list.append(_doc)

    embedding_model = OpenAIEmbeddings(model=EMBEDDING_NAME)

    vector_store = Chroma.from_documents(
        documents=document_list,
        embedding=embedding_model,
        collection_name=COLLECTION_NAME,
        persist_directory=PERSIST_DIRECTORY
    )

    print(len(document_list))

121
114
335


c:\Users\Playdata\SKN06\단위 프로젝트\Prj03\prj03\Lib\site-packages\langchain_community\document_loaders\parsers\pdf.py:322: UserWarning: Warning: Empty content on page 3 of document ./pdf/사건/조선\사건_조선_한산도해전.pdf
  warnings.warn(


391
175


In [4]:
# db 연결
embedding_model = OpenAIEmbeddings(model=EMBEDDING_NAME)
vector_store = Chroma(collection_name=COLLECTION_NAME, persist_directory=PERSIST_DIRECTORY, embedding_function=embedding_model)

In [6]:
vector_store._collection.count()

2792

In [7]:
vector_store.get()

{'ids': ['265b42ee-e947-4c41-9823-31b1cf20f5fc',
  '0b61db3c-7b26-4286-a133-600ce6244e0e',
  '567122f8-b686-4db5-9bc9-b973034ee2e8',
  'a8cbcf31-d345-4b3d-8212-56e390ebd454',
  'f8b5fbc4-5d80-4e53-af9e-ca02e67a387a',
  'a8d067af-3ce6-48d0-ba46-fb60f4c8798a',
  '079f4144-3d9d-4ac2-8c1f-9181983e04a8',
  '0908b1e0-2826-4951-b71a-3f4a53a8d9a6',
  '0a830439-d4be-466b-90b6-1383f4cdeae3',
  '9bc164c2-8769-40d8-8571-45024a4c254d',
  '7ead2c4b-b2aa-4b54-a51b-ddb6fe80619c',
  '67c98cdd-610f-49be-b23f-512f9c94b7d4',
  '90e957d8-ce54-4c5d-b4ae-533ac0d9cffd',
  'c2a7a9ad-7fae-4f6f-9a4c-458af3f0ce2f',
  'f17971ca-b18f-4d78-aca9-db51f52da6fd',
  'db1ae92a-6b31-4dc6-957c-4f73cecc122f',
  '64e0e201-221a-4e69-9e3c-770162344de7',
  'ec114e27-0c70-4362-b0c3-76bc9d865883',
  '0e23a3aa-09d1-4592-9837-96a2acf6f97b',
  '9333dae4-150b-4031-b873-db6278c83f40',
  '03415bf0-9cb7-4d94-9193-4d49a80f4633',
  '12a2cb17-74c0-42a3-befd-09556439f5dd',
  '42a33632-6357-48a2-80c4-39edae4599f5',
  '15224d2b-5f18-40bf-b768-

In [8]:
retriever = vector_store.as_retriever(search_type="mmr")

In [9]:
query = "이순신에 대해 알려줘"
result = retriever.invoke(query)
result

[Document(metadata={'full_text': '이순신[李舜臣]백전백승, 백의종군1545년(인종 1) ~ 1598년(선조 31) 이순신의 생애1545(인종 1)∼1598(선조 31). 조선의 무신이다. 무신으로 등용된 초기에는 북방 오랑캐를 방어하는 데 활약하였고, 일찍부터 장수로서 능력을 인정받았다. 그러나 원칙과 소신이 분명한 성격으로 인해 그를 질시하는 이들이 적지 않았다. 임진왜란 직전 우수한 장수로 특별히 발탁되어 전라좌수영에서 수군을 기르며 전쟁가능성에 대비했다. 전쟁이 발발하자 탁월한 전략, 전술적 능력을 발휘하여 연전연승했다. 이는 꾸준한 준비와 상황에 맞는 적절한 대응책 덕분이기도 했다. 그의 승리 덕분에 조선은 나라를 보전할 수 있었다. 그러나 빛나는 전공은 그를 질시하는 세력의견제를 불러왔고, 이로 인해 삼도수군통제사에서 물러나게 되었다. 하지만 곧 자리에 복귀하여무너진 수군을 재건했고 또 다시 일본군을 격파하였다. 노량해전에서 퇴각을 꾀하던 일본군에맞서 싸우다가 전사했다. 이순신의 유년기와 무신으로의 발탁12명종에서 선조로 이어지는 시기는 성리학을 깊이 익힌 사림들이 자신들의 학문을 정치로 펼치기위해 노력하던 시기였다. 북방 여진족과 남쪽의 왜구들이 조선의 국경을 침범하기도 했지만 그들보다 우수한 장수들이 이들을 격퇴하는 한편으로 무역과 관직수여를 통해 이들을 달래는 방책을 병행하기도 했다.이순신의 본관은 덕수. 자는 여해이다. 아버지는 이정이며, 어머니는 변수림(卞守琳)의 딸이다. 조부 이백록이 기묘사화에 희생된 이후 가세가 기울었으며, 그의 부친은관직에 뜻을 두지 않았다. 그러나 가풍은 엄격하였으며 학문과 문학적인 부분을 소홀히 하지 않았다. 특히 이순신의 어머니는 아들들을 아끼고 사랑하면서도 가정교육을 철저히 하였다. 정의감에 가득 차 불의를 참지 못하나 약한 자에게는 따뜻하게 대하던 이순신의 성격은 이러한 교육에 영향을 받았을 것이다.1572년에 훈련원에서 시행된 무과 별과시험에 응시하였으나 불행히도 말에서 떨어져 실격

In [10]:
result = vector_store.similarity_search_with_score(
    query="이순신에 대해 알려줘",
    k=5
)
result

[(Document(metadata={'full_text': '이순신[李舜臣]백전백승, 백의종군1545년(인종 1) ~ 1598년(선조 31) 이순신의 생애1545(인종 1)∼1598(선조 31). 조선의 무신이다. 무신으로 등용된 초기에는 북방 오랑캐를 방어하는 데 활약하였고, 일찍부터 장수로서 능력을 인정받았다. 그러나 원칙과 소신이 분명한 성격으로 인해 그를 질시하는 이들이 적지 않았다. 임진왜란 직전 우수한 장수로 특별히 발탁되어 전라좌수영에서 수군을 기르며 전쟁가능성에 대비했다. 전쟁이 발발하자 탁월한 전략, 전술적 능력을 발휘하여 연전연승했다. 이는 꾸준한 준비와 상황에 맞는 적절한 대응책 덕분이기도 했다. 그의 승리 덕분에 조선은 나라를 보전할 수 있었다. 그러나 빛나는 전공은 그를 질시하는 세력의견제를 불러왔고, 이로 인해 삼도수군통제사에서 물러나게 되었다. 하지만 곧 자리에 복귀하여무너진 수군을 재건했고 또 다시 일본군을 격파하였다. 노량해전에서 퇴각을 꾀하던 일본군에맞서 싸우다가 전사했다. 이순신의 유년기와 무신으로의 발탁12명종에서 선조로 이어지는 시기는 성리학을 깊이 익힌 사림들이 자신들의 학문을 정치로 펼치기위해 노력하던 시기였다. 북방 여진족과 남쪽의 왜구들이 조선의 국경을 침범하기도 했지만 그들보다 우수한 장수들이 이들을 격퇴하는 한편으로 무역과 관직수여를 통해 이들을 달래는 방책을 병행하기도 했다.이순신의 본관은 덕수. 자는 여해이다. 아버지는 이정이며, 어머니는 변수림(卞守琳)의 딸이다. 조부 이백록이 기묘사화에 희생된 이후 가세가 기울었으며, 그의 부친은관직에 뜻을 두지 않았다. 그러나 가풍은 엄격하였으며 학문과 문학적인 부분을 소홀히 하지 않았다. 특히 이순신의 어머니는 아들들을 아끼고 사랑하면서도 가정교육을 철저히 하였다. 정의감에 가득 차 불의를 참지 못하나 약한 자에게는 따뜻하게 대하던 이순신의 성격은 이러한 교육에 영향을 받았을 것이다.1572년에 훈련원에서 시행된 무과 별과시험에 응시하였으나 불행히도 말에서 떨어져 실

In [11]:
# Prompt Template 생성
messages = [
        ("ai", """
    너는 한국사에 대해서 해박한 지식을 가진 역사전문가야.
    내가 역사적 인물 또는 사건에 대해 말하면 그 인물과 사건을 이해가 쉽게, 흥미를 잃지 않게 쉬운용어로 풀어서 설명해주면 돼.

    문서에 없는 내용은 답변할 수 없습니다. 모른다고 답변 하세요.

    인물의 이름 :
    시대 :
    인물에 대해 알고 싶은 것 :
{context}"""),
        ("human", "{question}"),
    ]
prompt_template = ChatPromptTemplate(messages)

# 모델
model = ChatOpenAI(model="gpt-4o-mini")

# output parser
parser = StrOutputParser()

# Chain 구성 retriever(관련 문서 조회) -> prompt_template(prompt 생성) model(정답) -> output parser
chain = {"context":retriever, "question":RunnablePassthrough()} | prompt_template | model | parser

In [14]:
result = chain.invoke("이순신에 대해 알려줘") # 나옹혜근

In [15]:
print(result)

이순신(李舜臣)은 1545년(인종 1년)부터 1598년(선조 31년)까지 살았던 조선의 유명한 무신이자 장군입니다. 그는 임진왜란(1592-1598) 동안 조선 수군을 이끌며 일본군과의 해전에서 여러 차례 승리를 거두어 조선의 국방에 큰 기여를 했습니다.

이순신은 본관이 덕수이고, 자는 여해입니다. 그의 아버지는 이정이며, 어머니는 변수림의 딸입니다. 어린 시절부터 강한 정의감과 불의를 참지 못하는 성격을 지닌 그는, 무과에 응시하여 합격한 후 여러 지역에서 군사적 경험을 쌓았습니다. 

그는 임진왜란이 발발하기 전부터 일본의 침략 가능성을 예측하고 철저히 준비했습니다. 특히 그는 거북선이라는 독특한 전함을 이용해 해전에서 큰 전과를 올렸습니다. 그의 대표적인 전투로는 옥포해전, 한산도 대첩, 명량해전 등이 있으며, 이 전투들에서 일본군을 크게 무찌르고 조선 수군의 위세를 드높였습니다.

하지만 이순신은 그의 탁월한 능력 때문에 질시를 받기도 했고, 일시적으로 군직에서 물러나기도 했습니다. 그러나 그는 곧 복귀하여 다시 일본군과 싸웠습니다. 그의 마지막 전투는 노량해전으로, 이 전투에서 전사하게 되었습니다.

이순신의 유산은 지금까지도 이어져 오며, 그는 한국에서 국가의 영웅으로 추앙받고 있습니다. 그의 묘소는 아산에 위치하며, 여러 기념관과 동상이 그의 업적을 기리고 있습니다. 이순신은 단순한 군인이 아니라 조선의 역사에서 중요한 인물로 남아 있습니다.
